## LLM fine-tuning

Fine-tuning BERT: https://github.com/ShawhinT/YouTube-Blog/blob/main/LLMs/model-compression/2_quantize_model.ipynb


In [12]:
import json
file = json.load(open("llm-data.json", "r"))
print(file)

from datasets import Dataset

def format_prompt(example):
    return f"### Input: {example['input']}\n### Output: {json.dumps(example['output'])}<|endoftext|>"

formatted_data = [format_prompt(item) for item in file]
dataset = Dataset.from_dict({"text": formatted_data})


[{'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni didnt feel humiliated', 'output': 'sad'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni can go from feeling so hopeless to so damned hopeful just from being around someone who cares and is awake', 'output': 'sad'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\nim grabbing a minute to post i feel greedy wrong', 'output': 'angry'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni am ever feeling nostalgic about the fireplace i will know that it is still on the property', 'output': 'happy'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni am feeling grouchy', 'output': 'angry'}, {'input': 'Classi

In [13]:
from transformers import AutoModelForCausalLM, AutoTokenizer, Trainer, TrainingArguments

model_name = "microsoft/Phi-4-mini-instruct"  # change to your small model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name, device_map="cpu")

def tokenize(example):
    return tokenizer(example["text"], truncation=True, padding="max_length", max_length=128)

tokenized_dataset = dataset.map(tokenize, batched=True)


Fetching 2 files:   0%|          | 0/2 [01:25<?, ?it/s]


RuntimeError: Data processing error: CAS service error : IO Error: No space left on device (os error 28)

In [9]:
!pip install tf-keras

INFO: pip is looking at multiple versions of tf-keras to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 13.1 MB/s eta 0:00:00


In [ ]:
training_args = TrainingArguments(
    output_dir="./phi4-finetuned",
    per_device_train_batch_size=1,
    num_train_epochs=3,
    learning_rate=5e-5,
    logging_steps=1,
    save_steps=10,
    save_total_limit=1,
    no_cuda=True  # <-- important
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset,
    tokenizer=tokenizer
)

trainer.train()


In [ ]:
trainer.save_model("./phi4-finetuned")
tokenizer.save_pretrained("./phi4-finetuned")

## Unsloth

In [7]:
!pip install "unsloth[cu121-torch240] @ git+https://github.com/unslothai/unsloth.git"

  Cloning https://github.com/unslothai/unsloth.git to /private/var/folders/0s/lm29041s6hv5pq_lc3jblq540000gn/T/pip-install-6e_4w2_q/unsloth_314046af25144514913f83eb8805a8e2
  Running command git clone --filter=blob:none --quiet https://github.com/unslothai/unsloth.git /private/var/folders/0s/lm29041s6hv5pq_lc3jblq540000gn/T/pip-install-6e_4w2_q/unsloth_314046af25144514913f83eb8805a8e2
  Resolved https://github.com/unslothai/unsloth.git to commit 920b25b52cc8aaa310179bd6d4713f040b6bc0ce
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of unsloth to determine which version is compatible with other requirements. This could take a while.
ERROR: Package 'unsloth' requires a different Python: 3.8.19 not in '<=3.13,>=3.9'


In [1]:
!pip install unsloth trl peft accelerate bitsandbytes

In [3]:
import json
file = json.load(open("llm-data.json", "r"))
print(file)

[{'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni didnt feel humiliated', 'output': 'sad'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni can go from feeling so hopeless to so damned hopeful just from being around someone who cares and is awake', 'output': 'sad'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\nim grabbing a minute to post i feel greedy wrong', 'output': 'angry'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni am ever feeling nostalgic about the fireplace i will know that it is still on the property', 'output': 'happy'}, {'input': 'Classify this sentence with one of the emotions: angry, sad, happy, surprise, fear, disgust or neutral.\ni am feeling grouchy', 'output': 'angry'}, {'input': 'Classi

In [4]:
# For GPU check
import torch
print(f"CUDA available: {torch.cuda.is_available()}")
print(f"GPU: {torch.cuda.get_device_name(0) if torch.cuda.is_available() else 'None'}")

CUDA available: False
GPU: None


In [5]:
from unsloth import FastLanguageModel
import torch

model_name = "phi4-mini"

max_seq_length = 2048  # Choose sequence length
dtype = None  # Auto detection

# Load model and tokenizer
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name=model_name,
    max_seq_length=max_seq_length,
    dtype=dtype,
    load_in_4bit=True,
)

AssertionError: Torch not compiled with CUDA enabled

In [ ]:
from datasets import Dataset

def format_prompt(example):
    return f"### Input: {example['input']}\n### Output: {json.dumps(example['output'])}<|endoftext|>"

formatted_data = [format_prompt(item) for item in file]
dataset = Dataset.from_dict({"text": formatted_data})

In [ ]:
# Add LoRA adapters
model = FastLanguageModel.get_peft_model(
    model,
    r=64,  # LoRA rank - higher = more capacity, more memory
    target_modules=[
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ],
    lora_alpha=128,  # LoRA scaling factor (usually 2x rank)
    lora_dropout=0,  # Supports any, but = 0 is optimized
    bias="none",     # Supports any, but = "none" is optimized
    use_gradient_checkpointing="unsloth",  # Unsloth's optimized version
    random_state=3407,
    use_rslora=False,  # Rank stabilized LoRA
    loftq_config=None, # LoftQ
)

In [ ]:
from trl import SFTTrainer
from transformers import TrainingArguments

# Training arguments optimized for Unsloth
trainer = SFTTrainer(
    model=model,
    tokenizer=tokenizer,
    train_dataset=dataset,
    dataset_text_field="text",
    max_seq_length=max_seq_length,
    dataset_num_proc=2,
    args=TrainingArguments(
        per_device_train_batch_size=2,
        gradient_accumulation_steps=4,  # Effective batch size = 8
        warmup_steps=10,
        num_train_epochs=3,
        learning_rate=2e-4,
        fp16=not torch.cuda.is_bf16_supported(),
        bf16=torch.cuda.is_bf16_supported(),
        logging_steps=25,
        optim="adamw_8bit",
        weight_decay=0.01,
        lr_scheduler_type="linear",
        seed=3407,
        output_dir="outputs",
        save_strategy="epoch",
        save_total_limit=2,
        dataloader_pin_memory=False,
        report_to="none", # Disable Weights & Biases logging
    ),
)

In [ ]:
# Train the model
trainer_stats = trainer.train()

In [ ]:
# Test the fine-tuned model
FastLanguageModel.for_inference(model) # Enable native 2x faster inference

# Test prompt
messages = [
    {"role": "user", "content": "Extract the product information:\n<div class='product'><h2>iPad Air</h2><span class='price'>$1344</span><span class='category'>audio</span><span class='brand'>Dell</span></div>"},
]

inputs = tokenizer.apply_chat_template(
    messages,
    tokenize=True,
    add_generation_prompt=True,
    return_tensors="pt",
).to("cuda")

# Generate response
outputs = model.generate(
    input_ids=inputs,
    max_new_tokens=256,
    use_cache=True,
    temperature=0.7,
    do_sample=True,
    top_p=0.9,
)

# Decode and print
response = tokenizer.batch_decode(outputs)[0]
print(response)

In [ ]:
model.save_pretrained_gguf("gguf_model", tokenizer, quantization_method="q4_k_m")